# Damaged induced traps

This task will demonstrate how to model dynamic extrinsic traps in a FESTIM model. 

Research indicates that neutron-like damage in materials creates defects that trap hydrogen, potentially increasing hydrogen retention, which eventually saturates after a certain damage level. A proposed model aims to predict the temporal evolution of these damage-induced trap densities, considering the competition between hydrogen migration and trapping properties.

$$
\dfrac{\partial n_{i}}{\partial t} = \Phi \cdot K \left[1-\dfrac{n_{i}}{n_{\mathrm{max,}\Phi}}\right] - A \cdot n_{i}
$$

This equation describes the temporal evolution of trap density $n_{i}$.
The creation term, $\Phi \cdot K \left[1-\frac{n_{i}}{n_{\mathrm{max},\Phi}}\right]$, describes the number of traps formed by damage to a given saturation point $n_{\mathrm{max},\Phi}$.
$\Phi$ is the damage rate in dpa $\text{s}^{-1}$, and can vary spatially.
$K$ is the trap creation factor in traps $\text{m}^{-3} \text{dpa}^{-1}$.
$A$ is the trap annealing factor in $\text{s}^{-1}$ and is described as an Arrhenius law where $A = A_{0} \cdot \exp(-E_{A}/(k_{B} \cdot T))$.

We can use festim to show how such a trap may influence hydrogen retention in tungsten.

We will consider 2 models of 2mm of tungsten, one with a standard intrinsic trap, and another with a neutron-damage induced trap.

## FESTIM models

Let's start with a mesh and material properties. We will consider the diffusion transport properties from Frauenfelder. 

In [59]:
import numpy as np
import festim as F
import h_transport_materials as htm

# define mesh
my_mesh = F.MeshFromVertices(np.linspace(0, 2e-03, num=1000))

# define materials
D = htm.diffusivities.filter(material="tungsten").filter(author="frauenfelder")[0]
tungsten = F.Material(D_0=D.pre_exp.magnitude, E_D=D.act_energy.magnitude, id=1)
my_materials = F.Materials(
    [F.Material(D_0=D.pre_exp.magnitude, E_D=D.act_energy.magnitude, id=1)]
)


Next we can define the intrinsic and damage-induced extrinsic trap. We will consider the tungsten is being damaged at a rate of 5 dpa/fpy.

In [60]:

# define traps
lambda_val = 1.1e-10  # m
atom_density_W = 6.3222e28

trap_W = F.Trap(
    k_0=tungsten.D_0 / (lambda_val**2 * 6 * atom_density_W),
    E_k=tungsten.E_D,
    p_0=1e13,
    E_p=1.04,
    density=2.4e22,
    materials=tungsten,
)

fpy = 3600 * 24 * 365
trap_W_damage = F.NeutronInducedTrap(
    k_0=tungsten.D_0 / (lambda_val**2 * 6 * atom_density_W),
    E_k=tungsten.E_D,
    p_0=1e13,
    E_p=1.85,
    A_0=6.1838e-03,
    E_A=0.30,
    phi=5 / fpy,
    K=5.0e26,
    n_max=4.7e25,
    materials=tungsten,
)


Next we can define the other necessary parameters. The tungsten will be modelled at constant temperature of 800K and subjected to a source of hydrogen implanting on one surface at a flux of $10^{20}$ with an associated implantation depth of 3nm.

The simulation will be a transient simulating exposure in a full power year (fpy).

In [61]:

# define temperature
temperature = 800

# define boundary conditions
my_boundary_conditions = [
    F.ImplantationDirichlet(
        surfaces=1,
        phi=1e20,
        R_p=3e-09,
        D_0=tungsten.D_0,
        E_D=tungsten.E_D,
    ),
]

# define exports
my_exports = [
    F.DerivedQuantities(
        [F.TotalVolume("solute", volume=1)],
        show_units=True,
    ),
]

# define temporal settings
my_dt = F.Stepsize(
    initial_value=0.1,
    stepsize_change_ratio=1.1,
    dt_min=1e-1,
)

# define settings
my_settings = F.Settings(
    transient=True,
    final_time=fpy,
    absolute_tolerance=1e10,
    relative_tolerance=1e-10,
)


Let's now create a `F.Simulation()` object and fill it with parameters for a standard case and run the model:

In [62]:
results_folder = "task17/"
my_exports_standard = my_exports + [
    F.TXTExport(
        field="retention",
        filename=results_folder + "retention_profile_standard.txt",
    )
]

my_standard_model = F.Simulation(
    log_level=40,
    mesh=my_mesh,
    materials=my_materials,
    boundary_conditions=my_boundary_conditions,
    traps=F.Traps([trap_W]),
    temperature=temperature,
    exports=my_exports_standard,
    dt=my_dt,
    settings=my_settings
)
my_standard_model.initialise()
my_standard_model.run()


Defining initial values
Defining variational problem
Defining source terms
Defining boundary conditions
Time stepping...
100.0 %        3.2e+07 s    Elapsed time so far: 37.0 s


Let's run another simulation but accounting for the damage-induced trap:

In [63]:

my_exports_damaged = my_exports + [
    F.TXTExport(
        field="retention",
        filename=results_folder + "retention_profile_damaged.txt",
    )
]
my_damaged_model = F.Simulation(
    log_level=40,
    mesh=my_mesh,
    materials=my_materials,
    boundary_conditions=my_boundary_conditions,
    traps=F.Traps([trap_W, trap_W_damage]),
    temperature=temperature,
    exports=my_exports_damaged,
    dt=my_dt,
    settings=my_settings
)
my_damaged_model.initialise()
my_damaged_model.run()


Defining initial values
Defining variational problem
Defining source terms
Defining boundary conditions
Time stepping...
100.0 %        3.2e+07 s    Elapsed time so far: 40.8 s


## Results

We can plot the concentration profiles with or without the damage included over time in a GIF.
With very high levels of damage, it is clear that damage induced traps could have a huge impact on the results.

In [64]:
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML

# read results data
results_folder = "task17/"
data_standard = np.genfromtxt(
    results_folder + "retention_profile_standard.txt", delimiter=",", skip_header=1
)
data_damaged = np.genfromtxt(
    results_folder + "retention_profile_damaged.txt", delimiter=",", skip_header=1
)
times = my_damaged_model.exports[0].t

# Separate the x values and y values for each time step
x_standard, y_standard = data_standard[:, 0] * 1e3, data_standard[:, 1:]
x_damaged, y_damaged = data_damaged[:, 0] * 1e3, data_damaged[:, 1:]

# Set up the figure and axis
fig, ax = plt.subplots()
(line1,) = ax.plot([], [], lw=2, color="black", label="standard")
(line2,) = ax.plot([], [], lw=2, color="red", label="damaged")

# Initialization function to set up the background of each frame
def init():
    line1.set_data([], [])
    line2.set_data([], [])
    ax.set_xlim(0, 2)
    ax.set_ylim(1e14, 1e26)
    ax.set_yscale("log")
    ax.legend()
    ax.set_xlabel(r"x (mm)")
    ax.set_ylabel(r"T retention (m$^{-3}$)")
    ax.spines["top"].set_visible(False)
    ax.spines["right"].set_visible(False)

    return line1, line2


def animate(i):
    y1 = y_standard[:, i]
    y2 = y_damaged[:, i]
    line1.set_data(x_standard, y1)
    line2.set_data(x_damaged, y2)
    one_min, one_hour, one_day = 60, 3600, 3600 * 24
    t = times[i]  # NOTE this only works because both models have the same timesteps
    if t < one_min:
        ax.set_title(f"Time: {t:.1f} seconds")
    elif t < one_hour:
        ax.set_title(f"Time: {t/one_min:.1f} minutes")
    elif t < one_day:
        ax.set_title(f"Time: {t/one_hour:.1f} hours")
    else:
        ax.set_title(f"Time: {t/one_day:.1f} days")
    return line1, line2


# Call the animator
ani = animation.FuncAnimation(
    fig, animate, init_func=init, frames=y_damaged.shape[1], interval=50, blit=True
)

plt.close(fig)

# Display the animation in the Jupyter Notebook
HTML(ani.to_jshtml())